<a href="https://colab.research.google.com/github/AshvinVignesh/Final_year/blob/main/final_year_Randomforest_and_sampling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install deap


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.3/135.3 kB 4.1 MB/s eta 0:00:00


In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import numpy as np
from sklearn.model_selection import cross_val_score, KFold
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.multioutput import MultiOutputClassifier
from sklearn.metrics import classification_report , f1_score , make_scorer
from sklearn.model_selection import StratifiedKFold ,train_test_split ,GridSearchCV,cross_validate
from sklearn.tree import DecisionTreeClassifier
from sklearn.pipeline import Pipeline

In [ ]:
from sklearn.metrics import accuracy_score, classification_report
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler
# from imblearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier

In [ ]:
import pandas as pd
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import cross_val_score
# from deap import base, creator, tools, algorithms
import random
import numpy as np
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.preprocessing import LabelEncoder

In [ ]:
def custom_tokenizer(text):
    return text.split()

In [ ]:
df = pd.read_csv("Full_data_aspect_removed_words_Final.csv")
df.head(5)

original_text  \
0                        இரைச்சல் இல்லாத தெளிவான இசை   
1               harris romba naal kalichu super song   
2  hukum pondra iraichal padalai ketu kaathu vali...   
3           youtube la kuda editing nalla pannuvanga   
4                    amaran is also a diwali release   

                             sentences_with_pos_tags        lang sentiment  \
0      இரைச்சல்/NOUN இல்லாத/ADJ தெளிவான/ADJ இசை/NOUN       Tamil  POSITIVE   
1  harris/PROPN romba/ADV naal/NOUN kalichu/VERB ...  Code-Mixed  POSITIVE   
2  hukum/PROPN pondra/ADP iraichal/NOUN padalai/N...  Code-Mixed   NEUTRAL   
3  youtube/PROPN la/ADP kuda/ADV editing/NOUN nal...  Code-Mixed   NEUTRAL   
4  amaran/PROPN is/AUX also/ADV a/DET diwali/PROP...  Code-Mixed   NEUTRAL   

                                          clean_text  Acting  direction  \
0                        இரைச்சல் இல்லாத தெளிவான இசை       0          0   
1               harris romba naal kalichu super song       0          0   
2  hukum pondra iraichal padalai ketu kaathu vali...       0          0   
3              youtube kuda editing nalla pannuvanga       0          0   
4                              amaran diwali release       0          0   

   Music  VFX  Genre  excitement  ovr_sent  \
0      1    0      0           0         1   
1      1    0      0           0         1   
2      1    0      0           0         1   
3      0    1      0           0         1   
4      0    0      0           0         0   

                                          stop_words  
0                                    இல்லாத, தெளிவான  
1                               romba, naal, kalichu  
2  pondr, iraichal, ketu, kaathu, valichuruchu, a...  
3                                           la, kuda  
4                                        is, also, a

In [ ]:
N_ESTIMATORS_RANGE = [20, 60, 100, 150]
MAX_FEATURES_RANGE = ['sqrt', 'log2']
MAX_DEPTH_RANGE = [1,10, 50, 100, 200]
MIN_SAMPLES_SPLIT_RANGE = [0.1, 0.2 , 0.4, 0.8, ]
MIN_SAMPLES_LEAF_RANGE = [1, 2, 4, 6]

In [ ]:
X = df["clean_text"]



In [ ]:
def custom_mutation(individual, indpb):
    """Custom mutation that respects parameter types"""
    for i in range(len(individual)):
        if random.random() < indpb:
            if i == 0:  # n_estimators
                individual[i] = random.choice(N_ESTIMATORS_RANGE)
            elif i == 1:  # max_features
                individual[i] = random.choice(MAX_FEATURES_RANGE)
            elif i == 2:  # max_depth
                individual[i] = random.choice(MAX_DEPTH_RANGE)
            elif i == 3:  # min_samples_split
                individual[i] = random.choice(MIN_SAMPLES_SPLIT_RANGE)
            elif i == 4:  # min_samples_leaf
                individual[i] = random.choice(MIN_SAMPLES_LEAF_RANGE)
    return individual,

In [ ]:
def prepare_data(X, y_df):
    # Convert text to TF-IDF features
    vectorizer = TfidfVectorizer(max_features=1000)
    X_tfidf = vectorizer.fit_transform(X)

    # Prepare label encoders for each target
    label_encoders = {}
    y_encoded = pd.DataFrame()

    # Encode each target column
    for column in y_df.columns:
        le = LabelEncoder()
        y_encoded[column] = le.fit_transform(y_df[column].astype(str))
        label_encoders[column] = le

    return X_tfidf, y_encoded, label_encoders

def custom_f1_score(y_true, y_pred):
    return f1_score(y_true, y_pred, average='micro')

In [ ]:
creator.create("FitnessMax", base.Fitness, weights=(1.0,))
creator.create("Individual", list, fitness=creator.FitnessMax)

/usr/local/lib/python3.10/dist-packages/deap/creator.py:185: RuntimeWarning: A class named 'FitnessMax' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  warnings.warn("A class named '{0}' has already been created and it "
/usr/local/lib/python3.10/dist-packages/deap/creator.py:185: RuntimeWarning: A class named 'Individual' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  warnings.warn("A class named '{0}' has already been created and it "


In [ ]:
def create_toolbox(X, y_column):
    toolbox = base.Toolbox()

    # Define genes
    toolbox.register("n_estimators", random.choice, N_ESTIMATORS_RANGE)
    toolbox.register("max_features", random.choice, MAX_FEATURES_RANGE)
    toolbox.register("max_depth", random.choice, MAX_DEPTH_RANGE)
    toolbox.register("min_samples_split", random.choice, MIN_SAMPLES_SPLIT_RANGE)
    toolbox.register("min_samples_leaf", random.choice, MIN_SAMPLES_LEAF_RANGE)

    # Create individual and population
    toolbox.register("individual", tools.initCycle, creator.Individual,
                     (toolbox.n_estimators, toolbox.max_features, toolbox.max_depth,
                      toolbox.min_samples_split, toolbox.min_samples_leaf), n=1)

    toolbox.register("population", tools.initRepeat, list, toolbox.individual)

    # Define evaluation function
    def evaluate(individual):
      try:
          svc = SVC(
              C=individual[0],
              kernel=individual[1],
              gamma=individual[2],
              degree=individual[3] if individual[1] == 'poly' else 3,  # Default degree if not 'poly'
              random_state=42
          )
          scores = cross_val_score(svc, X, y_column, cv=3, scoring='f1_weighted')
          return scores.mean(),
      except Exception as e:
          print(f"Error with parameters: {individual}")
          print(f"Error message: {str(e)}")
          return 0.0,

    toolbox.register("evaluate", evaluate)

    # Genetic operators
    toolbox.register("mate", tools.cxTwoPoint)
    toolbox.register("mutate", custom_mutation, indpb=0.2)
    toolbox.register("select", tools.selTournament, tournsize=3)

    return toolbox

In [ ]:
def run_genetic_optimization(X, y_column, population_size=50, generations=30):
    toolbox = create_toolbox(X, y_column)

    # Create initial population
    population = toolbox.population(n=population_size)

    # Statistics setup
    stats = tools.Statistics(lambda ind: ind.fitness.values)
    stats.register("avg", np.mean)
    stats.register("std", np.std)
    stats.register("min", np.min)
    stats.register("max", np.max)

    # Run the algorithm
    final_pop, logbook = algorithms.eaSimple(population, toolbox,
                                           cxpb=0.7,
                                           mutpb=0.2,
                                           ngen=generations,
                                           stats=stats,
                                           verbose=True)

    # Get best solution
    best_solution = tools.selBest(final_pop, k=1)[0]

    # Convert to dictionary of parameters
    best_params = {
        'n_estimators': best_solution[0],
        'max_features': best_solution[1],
        'max_depth': best_solution[2],
        'min_samples_split': best_solution[3],
        'min_samples_leaf': best_solution[4]
    }

    return best_params, logbook

In [ ]:
def optimize_all_targets(X, y_df, population_size=50, generations=5):
    best_params_per_target = {}
    models = {}

    for column in y_df.columns:
        print(f"\nOptimizing for target: {column}")
        best_params, logbook = run_genetic_optimization(X, y_df[column],
                                                      population_size=population_size,
                                                      generations=generations)

        best_params_per_target[column] = best_params

        # Train final model with best parameters
        model = RandomForestClassifier(**best_params, random_state=42)
        model.fit(X, y_df[column])
        models[column] = model

        print(f"\nBest parameters for {column}:")
        for param, value in best_params.items():
            print(f"{param}: {value}")

    return best_params_per_target, models

In [ ]:
X_processed, y_encoded, label_encoders = prepare_data(
    df["clean_text"],
    y
)

In [ ]:
best_params_per_target, trained_models = optimize_all_targets(X_processed, y_encoded)


Optimizing for target: Acting
gen	nevals	avg     	std      	min     	max     
0  	50    	0.667915	0.0287143	0.644238	0.721188
1  	43    	0.694548	0.024278 	0.644238	0.72475 
2  	37    	0.710534	0.0158835	0.644238	0.72623 
3  	38    	0.718258	0.00888108	0.691819	0.72623 
4  	46    	0.717315	0.0184854 	0.644238	0.72623 
5  	38    	0.721675	0.015196  	0.644238	0.72623 

Best parameters for Acting:
n_estimators: 60
max_features: sqrt
max_depth: 200
min_samples_split: 0.2
min_samples_leaf: 1

Optimizing for target: direction
gen	nevals	avg     	std      	min     	max     
0  	50    	0.729739	0.0209113	0.716571	0.775702
1  	35    	0.746007	0.0239982	0.711628	0.774696
2  	38    	0.763013	0.0172075	0.716571	0.775139
3  	41    	0.77129 	0.00814587	0.717454	0.775532
4  	38    	0.768974	0.0141134 	0.716571	0.775532
5  	38    	0.772211	0.00703324	0.739319	0.775532

Best parameters for direction:
n_estimators: 60
max_features: sqrt
max_depth: 200
min_samples_split: 0.1
min_samples_leaf: 1

Optimiz

In [ ]:
print("\nBest parameters found:")
for param, value in best_params_per_target.items():
    print(f"{param}: {value}")


Best parameters found:
Acting: {'n_estimators': 60, 'max_features': 'sqrt', 'max_depth': 200, 'min_samples_split': 0.2, 'min_samples_leaf': 1}
direction: {'n_estimators': 60, 'max_features': 'sqrt', 'max_depth': 200, 'min_samples_split': 0.1, 'min_samples_leaf': 1}
Music: {'n_estimators': 150, 'max_features': 'sqrt', 'max_depth': 50, 'min_samples_split': 0.4, 'min_samples_leaf': 1}
Genre: {'n_estimators': 60, 'max_features': 'sqrt', 'max_depth': 200, 'min_samples_split': 0.2, 'min_samples_leaf': 4}
excitement: {'n_estimators': 150, 'max_features': 'sqrt', 'max_depth': 200, 'min_samples_split': 0.2, 'min_samples_leaf': 2}
ovr_sent: {'n_estimators': 100, 'max_features': 'log2', 'max_depth': 200, 'min_samples_split': 0.1, 'min_samples_leaf': 1}


In [ ]:
def prepare_data(df, aspect_column):
    """Prepare data for a specific aspect"""
    # Encode text to numerical values if needed
    # le = LabelEncoder()
    # Changed to return a DataFrame instead of a Series
    X = df[['clean_text']]
    y = df[aspect_column]
    return X, y

In [ ]:
def train_evaluate_model(X, y, sampling_strategy='none'):
    """Train and evaluate model with different sampling techniques"""
    skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    scores = []
    vectorizer = TfidfVectorizer(max_features=5000,
                                ngram_range=(1, 2),
                                min_df=2)

    # Transform features
    X_tfidf = vectorizer.fit_transform(X)

    for fold, (train_idx, val_idx) in enumerate(skf.split(X_tfidf, y)): # Split using the transformed data
        X_train, X_val = X_tfidf[train_idx], X_tfidf[val_idx] # Index the transformed data
        y_train, y_val = y[train_idx], y[val_idx]

        # Apply sampling strategy
        if sampling_strategy == 'oversample':
            sampler = SMOTE(random_state=42)
            X_train, y_train = sampler.fit_resample(X_train, y_train)
        elif sampling_strategy == 'undersample':
            sampler = RandomUnderSampler(random_state=42)
            X_train, y_train = sampler.fit_resample(X_train, y_train)

        # X_train = X_train.toarray()
        # X_val = X_val.toarray()

        if aspect == "acting":
          model =   RandomForestClassifier(random_state=42,n_estimators = 60, max_features = 'sqrt' , max_depth= 200, min_samples_split = 0.2, min_samples_leaf =1)
        elif aspect == "direction":
          model = RandomForestClassifier(random_state=42,n_estimators = 60, max_features = 'sqrt' , max_depth= 200, min_samples_split = 0.2, min_samples_leaf =1)
        elif aspect == "music":
          model = RandomForestClassifier(random_state=42,n_estimators = 60, max_features = 'sqrt' , max_depth= 200, min_samples_split = 0.2, min_samples_leaf =1)
        elif aspect == "genre":
          model = RandomForestClassifier(random_state=42,n_estimators = 60, max_features = 'sqrt' , max_depth= 200, min_samples_split = 0.2, min_samples_leaf =1)
        elif aspect == "excitement":
          model = RandomForestClassifier(random_state=42,n_estimators = 60, max_features = 'sqrt' , max_depth= 200, min_samples_split = 0.2, min_samples_leaf =1)
        elif aspect == "ovr_sent":
          model = RandomForestClassifier(random_state=42,n_estimators = 60, max_features = 'log' , max_depth= 200, min_samples_split = 0.2, min_samples_leaf =1)
        else:
          raise ValueError(f"Unknown aspect: {aspect}")

        # Train model
        # model = RandomForestClassifier(random_state=42,n_estimators = 60, max_features = 'sqrt' , max_depth= 200, min_samples_split = 0.2, min_samples_leaf =1)
        model.fit(X_train, y_train) # Remove reshape

        # Evaluate
        y_pred = model.predict(X_val) # Remove reshape
        score = accuracy_score(y_val, y_pred)
        scores.append(score)

        print(f"\nFold {fold + 1} Results:")
        print(classification_report(y_val, y_pred))

    return np.mean(scores), np.std(scores)

In [ ]:
def analyze_all_aspects_undersample(df, aspects):
    """Analyze all aspects with different sampling techniques"""
    results = {}
    # sampling_techniques = ['none', 'oversample', 'undersample']
    sampling_techniques = ['undersample']

    for aspect in aspects:
        print(f"\nAnalyzing aspect: {aspect}")
        X, y = prepare_data(df, aspect)

        aspect_results = {}
        for technique in sampling_techniques:
            print(f"\nUsing {technique} sampling:")
            mean_score, std_score = train_evaluate_model(X, y, technique)
            aspect_results[technique] = {
                'mean_accuracy': mean_score,
                'std_accuracy': std_score
            }
            print(f"Mean Accuracy: {mean_score:.4f} (±{std_score:.4f})")

        results[aspect] = aspect_results

    return results

In [ ]:
aspects = ['Acting', 'direction', 'Music',  'Genre', 'excitement','ovr_sent']
results = analyze_all_aspects_undersample(df, aspects)


Analyzing aspect: Acting

Using undersample sampling:

Fold 1 Results:
              precision    recall  f1-score   support

          -1       0.13      0.44      0.20        34
           0       0.87      0.79      0.83       770
           1       0.55      0.52      0.53       221

    accuracy                           0.72      1025
   macro avg       0.51      0.58      0.52      1025
weighted avg       0.77      0.72      0.74      1025


Fold 2 Results:
              precision    recall  f1-score   support

          -1       0.09      0.39      0.15        33
           0       0.87      0.78      0.82       769
           1       0.58      0.50      0.54       222

    accuracy                           0.71      1024
   macro avg       0.51      0.56      0.50      1024
weighted avg       0.78      0.71      0.74      1024


Fold 3 Results:
              precision    recall  f1-score   support

          -1       0.11      0.55      0.18        33
           0       0.89

In [ ]:
def analyze_all_aspects_oversample(df, aspects):
    """Analyze all aspects with different sampling techniques"""
    results = {}
    # sampling_techniques = ['none', 'oversample', 'undersample']
    sampling_techniques = ['oversample']

    for aspect in aspects:
        print(f"\nAnalyzing aspect: {aspect}")
        X, y = prepare_data(df, aspect)

        aspect_results = {}
        for technique in sampling_techniques:
            print(f"\nUsing {technique} sampling:")
            mean_score, std_score = train_evaluate_model(X, y, technique)
            aspect_results[technique] = {
                'mean_accuracy': mean_score,
                'std_accuracy': std_score
            }
            print(f"Mean Accuracy: {mean_score:.4f} (±{std_score:.4f})")

        results[aspect] = aspect_results

    return results

In [ ]:
aspects = ['Acting', 'direction', 'Music',  'Genre', 'excitement','ovr_sent']
results = analyze_all_aspects_oversample(df, aspects)


Analyzing aspect: Acting

Using oversample sampling:

Fold 1 Results:
              precision    recall  f1-score   support

          -1       0.16      0.21      0.18        34
           0       0.89      0.88      0.88       770
           1       0.63      0.61      0.62       221

    accuracy                           0.80      1025
   macro avg       0.56      0.57      0.56      1025
weighted avg       0.81      0.80      0.80      1025


Fold 2 Results:
              precision    recall  f1-score   support

          -1       0.18      0.27      0.22        33
           0       0.88      0.87      0.87       769
           1       0.63      0.61      0.62       222

    accuracy                           0.79      1024
   macro avg       0.56      0.58      0.57      1024
weighted avg       0.80      0.79      0.80      1024


Fold 3 Results:
              precision    recall  f1-score   support

          -1       0.24      0.42      0.30        33
           0       0.89 

In [ ]:
def train_final_models_grid_search(df, aspects):
    """
    For each aspect, perform a grid search to find the best SVC parameters using a pipeline.
    Uses an 80/20 train-test split, prints training and test accuracy and classification reports,
    and returns the best models along with their label encoders.
    """
    best_models = {}
    train_reports = {}
    test_reports = {}

    # Define a parameter grid for the SVC inside a pipeline
    param_grid = {
        'clf__n_estimators': [50, 100, 200],
        'clf__max_depth': [None, 10, 20, 30],
        'clf__min_samples_split': [2, 5, 10],
        'clf__min_samples_leaf': [1, 2, 4]
    }

    for aspect in aspects:
        print(f"\n=== Processing aspect: {aspect} ===")
        X, y = prepare_data(df, aspect)
        # Encode target labels to numerical values
        le = LabelEncoder()
        y_encoded = le.fit_transform(y)

        # Split data into training and testing sets (80/20 split)
        X_train, X_test, y_train, y_test = train_test_split(
            X, y_encoded, test_size=0.2, random_state=42, stratify=y_encoded
        )

        # Create a pipeline: first vectorize text, then classify with SVC
        pipeline = Pipeline([
            ('tfidf', TfidfVectorizer(max_features=5000,
                                      ngram_range=(1, 2),
                                      min_df=2,
                                      max_df=0.95)),
            ('clf', RandomForestClassifier(random_state=42))
        ])

        # Set up GridSearchCV with 5-fold cross-validation
        cv_strategy = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
        grid = GridSearchCV(pipeline, param_grid, cv=cv_strategy, scoring='accuracy', n_jobs=-1)
        grid.fit(X_train['clean_text'], y_train)

        print(f"Best parameters for aspect '{aspect}': {grid.best_params_}")

        best_estimator = grid.best_estimator_

        # Evaluate on training data
        y_train_pred = best_estimator.predict(X_train['clean_text'])
        train_acc = accuracy_score(y_train, y_train_pred)
        print("Training Accuracy: {:.4f}".format(train_acc))
        train_report = classification_report(y_train, y_train_pred)
        print("Training Classification Report:\n", train_report)

        # Evaluate on test data
        y_test_pred = best_estimator.predict(X_test['clean_text'])
        test_acc = accuracy_score(y_test, y_test_pred)
        print("Test Accuracy: {:.4f}".format(test_acc))
        test_report = classification_report(y_test, y_test_pred)
        print("Test Classification Report:\n", test_report)

        best_models[aspect.lower()] = {
            "model": best_estimator,
            "label_encoder": le
        }
        train_reports[aspect.lower()] = train_report
        test_reports[aspect.lower()] = test_report

    return best_models, train_reports, test_reports

In [ ]:
def predict_all_aspects(sentence, final_models):
    """
    Given a sentence, predict its sentiment for all aspects using the final trained models.
    Returns a dictionary with aspect names as keys and predicted labels as values.
    """
    predictions = {}
    for aspect, model_info in final_models.items():
        model = model_info['model']
        le = model_info['label_encoder']
        # The pipeline expects raw text
        pred_encoded = model.predict([sentence])[0]
        pred_label = le.inverse_transform([pred_encoded])[0]
        predictions[aspect] = pred_label
    return predictions

In [ ]:
aspects = ['Acting', 'direction', 'Music',  'Genre', 'excitement','ovr_sent']

In [ ]:
best_models, train_reports, test_reports = train_final_models_grid_search(df, aspects)


=== Processing aspect: Acting ===
Best parameters for aspect 'Acting': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 5, 'clf__n_estimators': 100}
Training Accuracy: 0.8980
Training Classification Report:
               precision    recall  f1-score   support

           0       0.83      0.04      0.07       132
           1       0.91      0.98      0.94      2966
           2       0.85      0.76      0.80       843

    accuracy                           0.90      3941
   macro avg       0.86      0.59      0.60      3941
weighted avg       0.89      0.90      0.88      3941

Test Accuracy: 0.8418
Test Classification Report:
               precision    recall  f1-score   support

           0       1.00      0.03      0.06        33
           1       0.87      0.94      0.91       742
           2       0.70      0.61      0.65       211

    accuracy                           0.84       986
   macro avg       0.86      0.53      0.54       986
wei

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


Best parameters for aspect 'excitement': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 10, 'clf__n_estimators': 200}
Training Accuracy: 0.8132
Training Classification Report:
               precision    recall  f1-score   support

           0       0.92      0.50      0.65       594
           1       0.78      0.94      0.86      2244
           2       0.86      0.72      0.78      1103

    accuracy                           0.81      3941
   macro avg       0.85      0.72      0.76      3941
weighted avg       0.83      0.81      0.80      3941

Test Accuracy: 0.6785
Test Classification Report:
               precision    recall  f1-score   support

           0       0.67      0.20      0.30       148
           1       0.67      0.87      0.76       562
           2       0.70      0.55      0.62       276

    accuracy                           0.68       986
   macro avg       0.68      0.54      0.56       986
weighted avg       0.68      0.68

# with df 3

In [ ]:
df = pd.read_csv("fyp_data.csv")
def train_final_models_grid_search(df, aspects):
    """
    For each aspect, perform a grid search to find the best SVC parameters using a pipeline.
    Uses an 80/20 train-test split, prints training and test accuracy and classification reports,
    and returns the best models along with their label encoders.
    """
    best_models = {}
    train_reports = {}
    test_reports = {}

    # Define a parameter grid for the SVC inside a pipeline
    param_grid = {
        'clf__n_estimators': [50, 100, 200],
        'clf__max_depth': [None, 10, 20, 30],
        'clf__min_samples_split': [2, 5, 10],
        'clf__min_samples_leaf': [1, 2, 4]
    }

    for aspect in aspects:
        print(f"\n=== Processing aspect: {aspect} ===")
        X, y = prepare_data(df, aspect)
        # Encode target labels to numerical values
        le = LabelEncoder()
        y_encoded = le.fit_transform(y)

        # Split data into training and testing sets (80/20 split)
        X_train, X_test, y_train, y_test = train_test_split(
            X, y_encoded, test_size=0.2, random_state=42, stratify=y_encoded
        )

        # Create a pipeline: first vectorize text, then classify with SVC
        pipeline = Pipeline([
            ('tfidf', TfidfVectorizer(max_features=5000,
                                      ngram_range=(1, 2),
                                      min_df=3,
                                      max_df=0.90)),
            ('clf', RandomForestClassifier(random_state=42))
        ])

        # Set up GridSearchCV with 5-fold cross-validation
        cv_strategy = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
        grid = GridSearchCV(pipeline, param_grid, cv=cv_strategy, scoring='accuracy', n_jobs=-1)
        grid.fit(X_train['clean_text'], y_train)

        print(f"Best parameters for aspect '{aspect}': {grid.best_params_}")

        best_estimator = grid.best_estimator_

        # Evaluate on training data
        y_train_pred = best_estimator.predict(X_train['clean_text'])
        train_acc = accuracy_score(y_train, y_train_pred)
        print("Training Accuracy: {:.4f}".format(train_acc))
        train_report = classification_report(y_train, y_train_pred)
        print("Training Classification Report:\n", train_report)

        # Evaluate on test data
        y_test_pred = best_estimator.predict(X_test['clean_text'])
        test_acc = accuracy_score(y_test, y_test_pred)
        print("Test Accuracy: {:.4f}".format(test_acc))
        test_report = classification_report(y_test, y_test_pred)
        print("Test Classification Report:\n", test_report)

        best_models[aspect.lower()] = {
            "model": best_estimator,
            "label_encoder": le
        }
        train_reports[aspect.lower()] = train_report
        test_reports[aspect.lower()] = test_report

    return best_models, train_reports, test_reports

In [ ]:
best_models, train_reports, test_reports = train_final_models_grid_search(df, aspects)


=== Processing aspect: Acting ===
Best parameters for aspect 'Acting': {'clf__max_depth': None, 'clf__min_samples_leaf': 1, 'clf__min_samples_split': 5, 'clf__n_estimators': 100}
Training Accuracy: 0.9820
Training Classification Report:
               precision    recall  f1-score   support

           0       1.00      0.76      0.86       132
           1       0.98      1.00      0.99      2966
           2       0.99      0.96      0.97       843

    accuracy                           0.98      3941
   macro avg       0.99      0.91      0.94      3941
weighted avg       0.98      0.98      0.98      3941

Test Accuracy: 0.8499
Test Classification Report:
               precision    recall  f1-score   support

           0       0.33      0.03      0.06        33
           1       0.89      0.94      0.91       742
           2       0.72      0.67      0.69       211

    accuracy                           0.85       986
   macro avg       0.64      0.55      0.55       986
wei

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/m

Best parameters for aspect 'excitement': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 10, 'clf__n_estimators': 200}
Training Accuracy: 0.8153
Training Classification Report:
               precision    recall  f1-score   support

           0       0.91      0.51      0.65       594
           1       0.79      0.93      0.86      2244
           2       0.85      0.74      0.79      1103

    accuracy                           0.82      3941
   macro avg       0.85      0.73      0.77      3941
weighted avg       0.83      0.82      0.81      3941

Test Accuracy: 0.6694
Test Classification Report:
               precision    recall  f1-score   support

           0       0.59      0.18      0.28       148
           1       0.67      0.86      0.75       562
           2       0.69      0.54      0.60       276

    accuracy                           0.67       986
   macro avg       0.65      0.53      0.55       986
weighted avg       0.66      0.67

#with df min 5

In [ ]:
train_df = pd.read_csv("train_data.csv")
test_df = pd.read_csv("test_data.csv")
def train_final_models_grid_search(train_df,test_df, aspects):
    """
    For each aspect, perform a grid search to find the best SVC parameters using a pipeline.
    Uses an 80/20 train-test split, prints training and test accuracy and classification reports,
    and returns the best models along with their label encoders.
    """
    best_models = {}
    train_reports = {}
    test_reports = {}

    # Define a parameter grid for the SVC inside a pipeline
    param_grid = {
        'clf__n_estimators': [50, 100, 200],
        'clf__max_depth': [None],
        'clf__min_samples_split': [2, 5, 10],
        'clf__min_samples_leaf': [2, 4,8]
    }

    for aspect in aspects:
        print(f"\n=== Processing aspect: {aspect} ===")
        X_train, y_train = prepare_data(train_df, aspect)
        X_test, y_test = prepare_data(test_df, aspect)

        # Encode target labels to numerical values
        le = LabelEncoder()
        y_train_encoded = le.fit_transform(y_train)
        y_test_encoded = le.fit_transform(y_test)
        target_names = [str(label) for label in le.classes_]


        # Create a pipeline: first vectorize text, then classify with SVC
        pipeline = Pipeline([
            ('tfidf', TfidfVectorizer(max_features=5000,
                                      ngram_range=(1, 2),
                                      min_df=5,
                                      max_df=0.90,
                                      tokenizer=custom_tokenizer)),
            ('clf', RandomForestClassifier(random_state=42,class_weight='balanced'))
        ])

        # Set up GridSearchCV with 5-fold cross-validation
        cv_strategy = StratifiedKFold(n_splits=10, shuffle=True, random_state=42)
        grid = GridSearchCV(pipeline, param_grid, cv=cv_strategy, scoring='balanced_accuracy', n_jobs=-1,return_train_score=True)
        X_train = X_train.dropna(subset=['clean_text'])
        X_train = X_train[X_train['clean_text'].str.strip() != '']
        grid.fit(X_train['clean_text'], y_train_encoded)

        mean_train_accuracy = grid.cv_results_['mean_train_score'][grid.best_index_]
        print(f"Average Training Accuracy across folds for aspect '{aspect}': {mean_train_accuracy:.4f}")

        print(f"Best parameters for aspect '{aspect}': {grid.best_params_}")

        best_estimator = grid.best_estimator_

        # Evaluate on training data
        y_train_pred = best_estimator.predict(X_train['clean_text'])
        train_acc = accuracy_score(y_train_encoded, y_train_pred)
        print("Training Accuracy: {:.4f}".format(train_acc))
        train_report = classification_report(y_train_encoded, y_train_pred)
        print("Training Classification Report:\n", train_report)

        # Evaluate on test data
        y_test_pred = best_estimator.predict(X_test['clean_text'])
        test_acc = accuracy_score(y_test_encoded, y_test_pred)
        print("Test Accuracy: {:.4f}".format(test_acc))
        test_report = classification_report(y_test_encoded, y_test_pred)
        print("Test Classification Report:\n", test_report)

        best_models[aspect.lower()] = {
            "model": best_estimator,
            "label_encoder": le
        }
        train_reports[aspect.lower()] = train_report
        test_reports[aspect.lower()] = test_report

    return best_models, train_reports, test_reports

In [ ]:
aspects = ['Acting', 'direction', 'Music','ovr_sent']

In [ ]:
best_models, train_reports, test_reports = train_final_models_grid_search(train_df,test_df, aspects)


=== Processing aspect: Acting ===


/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Average Training Accuracy across folds for aspect 'Acting': 0.8495
Best parameters for aspect 'Acting': {'clf__max_depth': None, 'clf__min_samples_leaf': 4, 'clf__min_samples_split': 2, 'clf__n_estimators': 100}
Training Accuracy: 0.8505
Training Classification Report:
               precision    recall  f1-score   support

           0       0.46      0.90      0.61       131
           1       0.94      0.86      0.90      2962
           2       0.70      0.80      0.74       848

    accuracy                           0.85      3941
   macro avg       0.70      0.85      0.75      3941
weighted avg       0.87      0.85      0.86      3941

Test Accuracy: 0.7860
Test Classification Report:
               precision    recall  f1-score   support

           0       0.13      0.21      0.16        34
           1       0.89      0.84      0.87       746
           2       0.60      0.67      0.64       206

    accuracy                           0.79       986
   macro avg       0.54  

/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Average Training Accuracy across folds for aspect 'direction': 0.8807
Best parameters for aspect 'direction': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 5, 'clf__n_estimators': 200}
Training Accuracy: 0.8531
Training Classification Report:
               precision    recall  f1-score   support

           0       0.57      0.88      0.69       568
           1       0.98      0.85      0.91      3128
           2       0.58      0.89      0.70       245

    accuracy                           0.85      3941
   macro avg       0.71      0.87      0.77      3941
weighted avg       0.90      0.85      0.86      3941

Test Accuracy: 0.7363
Test Classification Report:
               precision    recall  f1-score   support

           0       0.31      0.54      0.40       124
           1       0.91      0.78      0.84       804
           2       0.38      0.53      0.44        58

    accuracy                           0.74       986
   macro avg       

/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Average Training Accuracy across folds for aspect 'Music': 0.9447
Best parameters for aspect 'Music': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 10, 'clf__n_estimators': 100}
Training Accuracy: 0.9665
Training Classification Report:
               precision    recall  f1-score   support

           0       0.66      0.94      0.77        89
           1       1.00      0.98      0.99      3446
           2       0.83      0.90      0.86       406

    accuracy                           0.97      3941
   macro avg       0.83      0.94      0.87      3941
weighted avg       0.97      0.97      0.97      3941

Test Accuracy: 0.9402
Test Classification Report:
               precision    recall  f1-score   support

           0       0.33      0.44      0.38        18
           1       0.98      0.97      0.98       867
           2       0.74      0.75      0.75       101

    accuracy                           0.94       986
   macro avg       0.68   

/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Average Training Accuracy across folds for aspect 'ovr_sent': 0.8119
Best parameters for aspect 'ovr_sent': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 5, 'clf__n_estimators': 50}
Training Accuracy: 0.8102
Training Classification Report:
               precision    recall  f1-score   support

           0       0.78      0.84      0.81      1346
           1       0.59      0.81      0.68       567
           2       0.93      0.79      0.86      2028

    accuracy                           0.81      3941
   macro avg       0.77      0.81      0.78      3941
weighted avg       0.83      0.81      0.82      3941

Test Accuracy: 0.6450
Test Classification Report:
               precision    recall  f1-score   support

           0       0.65      0.65      0.65       348
           1       0.32      0.54      0.40       139
           2       0.83      0.67      0.74       499

    accuracy                           0.65       986
   macro avg       0.6

In [ ]:
train_df = pd.read_csv("train_data.csv")
test_df = pd.read_csv("test_data.csv")
def train_final_models_grid_search(train_df,test_df, aspects):
    """
    For each aspect, perform a grid search to find the best SVC parameters using a pipeline.
    Uses an 80/20 train-test split, prints training and test accuracy and classification reports,
    and returns the best models along with their label encoders.
    """
    best_models = {}
    train_reports = {}
    test_reports = {}

    # Define a parameter grid for the SVC inside a pipeline
    param_grid = {
        'clf__n_estimators': [50, 100, 200],
        'clf__max_depth': [None],
        'clf__min_samples_split': [2, 5, 10],
        'clf__min_samples_leaf': [2, 4,8]
    }

    for aspect in aspects:
        print(f"\n=== Processing aspect: {aspect} ===")
        X_train, y_train = prepare_data(train_df, aspect)
        X_test, y_test = prepare_data(test_df, aspect)

        # Encode target labels to numerical values
        le = LabelEncoder()
        y_train_encoded = le.fit_transform(y_train)
        y_test_encoded = le.fit_transform(y_test)
        target_names = [str(label) for label in le.classes_]


        # Create a pipeline: first vectorize text, then classify with SVC
        pipeline = Pipeline([
            ('tfidf', TfidfVectorizer(max_features=5000,
                                      ngram_range=(1, 2),
                                      min_df=5,
                                      max_df=0.90,
                                      tokenizer=custom_tokenizer)),
            ('clf', RandomForestClassifier(random_state=42,class_weight='balanced'))
        ])

        # Set up GridSearchCV with 5-fold cross-validation
        cv_strategy = StratifiedKFold(n_splits=10, shuffle=True, random_state=42)
        grid = GridSearchCV(pipeline, param_grid, cv=cv_strategy, scoring='balanced_accuracy', n_jobs=-1,return_train_score=True)
        X_train = X_train.dropna(subset=['clean_text'])
        X_train = X_train[X_train['clean_text'].str.strip() != '']
        grid.fit(X_train['clean_text'], y_train_encoded)

        mean_train_accuracy = grid.cv_results_['mean_train_score'][grid.best_index_]
        print(f"Average Training Accuracy across folds for aspect '{aspect}': {mean_train_accuracy:.4f}")

        print(f"Best parameters for aspect '{aspect}': {grid.best_params_}")
        model = RandomForestClassifier(
          random_state=42,
          n_estimators=grid.best_params_.get("n_estimators", 100),  # Default to 100 if not found
          max_depth=grid.best_params_.get("max_depth", None),  # Default to "sqrt"
          min_samples_split=grid.best_params_.get("min_samples_split", 8),  # Default to 2
          min_samples_leaf=grid.best_params_.get("min_samples_leaf", 5)   # Default to 1
        )
        vectorizer = TfidfVectorizer(max_features=5000, ngram_range=(1, 2),
                              min_df=5, max_df=0.90, tokenizer=custom_tokenizer)
        X_train_transformed = vectorizer.fit_transform(X_train['clean_text'])
        X_test_transformed = vectorizer.transform(X_test['clean_text'])
        model.fit(X_train_transformed, y_train_encoded)
        best_estimator = grid.best_estimator_

        # Evaluate on training data
        y_train_pred = best_estimator.predict(X_train['clean_text'])
        train_acc = accuracy_score(y_train_encoded, y_train_pred)
        print("Training Accuracy best estimator: {:.4f}".format(train_acc))

        train_report = classification_report(y_train_encoded, y_train_pred)
        print("Training Classification Report best_estimator:\n", train_report)

        # Evaluate on test data
        y_test_pred = best_estimator.predict(X_test['clean_text'])
        test_acc = accuracy_score(y_test_encoded, y_test_pred)
        print("Test Accuracy best_estimator: {:.4f}".format(test_acc))
        test_report = classification_report(y_test_encoded, y_test_pred)
        print("Test Classification Report best_estimator:\n", test_report)


        y_train_pred_new = model.predict(X_train_transformed)
        train_acc_new = accuracy_score(y_train_encoded, y_train_pred_new)
        print("Training Accuracy new : {:.4f}".format(train_acc_new))
        y_test_pred_new = model.predict(X_test_transformed)
        test_acc_new = accuracy_score(y_test_encoded, y_test_pred_new)
        print("New Test Accuracy: {:.4f}".format(test_acc_new))

        best_models[aspect.lower()] = {
            "model": best_estimator,
            "label_encoder": le
        }
        train_reports[aspect.lower()] = train_report
        test_reports[aspect.lower()] = test_report

    return best_models, train_reports, test_reports

In [ ]:
best_models, train_reports, test_reports = train_final_models_grid_search(train_df,test_df, aspects)


=== Processing aspect: Acting ===


/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Average Training Accuracy across folds for aspect 'Acting': 0.8495
Best parameters for aspect 'Acting': {'clf__max_depth': None, 'clf__min_samples_leaf': 4, 'clf__min_samples_split': 2, 'clf__n_estimators': 100}


/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Training Accuracy best estimator: 0.8505
Training Classification Report best_estimator:
               precision    recall  f1-score   support

           0       0.46      0.90      0.61       131
           1       0.94      0.86      0.90      2962
           2       0.70      0.80      0.74       848

    accuracy                           0.85      3941
   macro avg       0.70      0.85      0.75      3941
weighted avg       0.87      0.85      0.86      3941

Test Accuracy best_estimator: 0.7860
Test Classification Report best_estimator:
               precision    recall  f1-score   support

           0       0.13      0.21      0.16        34
           1       0.89      0.84      0.87       746
           2       0.60      0.67      0.64       206

    accuracy                           0.79       986
   macro avg       0.54      0.57      0.56       986
weighted avg       0.81      0.79      0.80       986

Training Accuracy new : 0.8716
New Test Accuracy: 0.8377

=== Proces

...

Training Accuracy best estimator: 0.9665
Training Classification Report best_estimator:
               precision    recall  f1-score   support

           0       0.66      0.94      0.77        89
           1       1.00      0.98      0.99      3446
           2       0.83      0.90      0.86       406

    accuracy                           0.97      3941
   macro avg       0.83      0.94      0.87      3941
weighted avg       0.97      0.97      0.97      3941

Test Accuracy best_estimator: 0.9402
Test Classification Report best_estimator:
               precision    recall  f1-score   support

           0       0.33      0.44      0.38        18
           1       0.98      0.97      0.98       867
           2       0.74      0.75      0.75       101

    accuracy                           0.94       986
   macro avg       0.68      0.72      0.70       986
weighted avg       0.94      0.94      0.94       986

Training Accuracy new : 0.9447
New Test Accuracy: 0.9533

=== Proces

/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Average Training Accuracy across folds for aspect 'ovr_sent': 0.8119
Best parameters for aspect 'ovr_sent': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 5, 'clf__n_estimators': 50}


/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Training Accuracy best estimator: 0.8102
Training Classification Report best_estimator:
               precision    recall  f1-score   support

           0       0.78      0.84      0.81      1346
           1       0.59      0.81      0.68       567
           2       0.93      0.79      0.86      2028

    accuracy                           0.81      3941
   macro avg       0.77      0.81      0.78      3941
weighted avg       0.83      0.81      0.82      3941

Test Accuracy best_estimator: 0.6450
Test Classification Report best_estimator:
               precision    recall  f1-score   support

           0       0.65      0.65      0.65       348
           1       0.32      0.54      0.40       139
           2       0.83      0.67      0.74       499

    accuracy                           0.65       986
   macro avg       0.60      0.62      0.60       986
weighted avg       0.69      0.65      0.66       986

Training Accuracy new : 0.7353
New Test Accuracy: 0.6765


In [ ]:
train_df = pd.read_csv("train_data.csv")
test_df = pd.read_csv("test_data.csv")
def train_final_models_grid_search(train_df, test_df, aspects):
    """
    For each aspect:
    1. Perform grid search on the training data to find the best parameters.
    2. Using the best parameters, perform 10-fold cross-validation,
       returning both the average accuracy and the list of fold estimators.
    3. Select the best estimator from CV (highest test score) and evaluate it on test data.
    Returns the best models along with their label encoders and classification reports.
    """
    best_models = {}
    train_reports = {}
    test_reports = {}

    # Parameter grid for the classifier
    param_grid = {
        'clf__n_estimators': [50, 100, 200],
        'clf__max_depth': [None],
        'clf__min_samples_split': [2, 5, 10],
        'clf__min_samples_leaf': [2, 4, 8]
    }

    for aspect in aspects:
        print(f"\n=== Processing aspect: {aspect} ===")
        # Prepare data for current aspect
        X_train, y_train = prepare_data(train_df, aspect)
        X_test, y_test = prepare_data(test_df, aspect)

        # Encode target labels to numerical values
        le = LabelEncoder()
        y_train_encoded = le.fit_transform(y_train)
        y_test_encoded = le.fit_transform(y_test)

        # Build initial pipeline with a placeholder classifier
        pipeline = Pipeline([
            ('tfidf', TfidfVectorizer(max_features=5000,
                                      ngram_range=(1, 2),
                                      min_df=5,
                                      max_df=0.90,
                                      tokenizer=custom_tokenizer)),
            ('clf', RandomForestClassifier(random_state=42, class_weight='balanced'))
        ])

        # 10-fold CV strategy for grid search
        cv_strategy = StratifiedKFold(n_splits=10, shuffle=True, random_state=42)

        # Ensure there are no missing or empty texts in training set
        X_train = X_train.dropna(subset=['clean_text'])
        X_train = X_train[X_train['clean_text'].str.strip() != '']

        # --- Step 1: Grid Search ---
        grid = GridSearchCV(pipeline, param_grid, cv=cv_strategy,
                            scoring='balanced_accuracy', n_jobs=-1, return_train_score=True)
        grid.fit(X_train['clean_text'], y_train_encoded)
        best_params = grid.best_params_
        print(f"Best parameters for aspect '{aspect}': {best_params}")

        # --- Step 2: Build a new pipeline using the best parameters ---
        best_pipeline = Pipeline([
            ('tfidf', TfidfVectorizer(max_features=5000,
                                      ngram_range=(1, 2),
                                      min_df=5,
                                      max_df=0.90,
                                      tokenizer=custom_tokenizer)),
            ('clf', RandomForestClassifier(random_state=42,
                                             class_weight='balanced',
                                             n_estimators=best_params['clf__n_estimators'],
                                             max_depth=best_params['clf__max_depth'],
                                             min_samples_split=best_params['clf__min_samples_split'],
                                             min_samples_leaf=best_params['clf__min_samples_leaf']))
        ])

        # --- Step 3: Perform 10-Fold Cross Validation with estimator return ---
        cv_results = cross_validate(best_pipeline, X_train['clean_text'], y_train_encoded,
                                    cv=StratifiedKFold(n_splits=10, shuffle=True, random_state=42),
                                    scoring='balanced_accuracy', return_train_score=True,return_estimator=True, n_jobs=-1)
        avg_cv_score_test = cv_results['test_score'].mean()
        avg_cv_score_train = cv_results['train_score'].mean()
        print(avg_cv_score_test)
        print(avg_cv_score_train)


        print(f"Average 10-fold CV test Accuracy for aspect '{aspect}': {avg_cv_score_test:.4f}")
        print(f"Average 10-fold CV train Accuracy for aspect '{aspect}': {avg_cv_score_train:.4f}")

        # --- Step 4: Select the best estimator from the CV folds ---
        best_index = np.argmax(cv_results['test_score'])
        best_cv_estimator = cv_results['estimator'][best_index]

        # Evaluate the selected estimator on the training data (optional)
        y_train_pred = best_cv_estimator.predict(X_train['clean_text'])
        train_acc = accuracy_score(y_train_encoded, y_train_pred)
        print("Final Training Accuracy: {:.4f}".format(train_acc))
        train_report = classification_report(y_train_encoded, y_train_pred)
        print("Final Training Classification Report:\n", train_report)

        # --- Step 5: Evaluate on Test Data ---
        y_test_pred = best_cv_estimator.predict(X_test['clean_text'])
        test_acc = accuracy_score(y_test_encoded, y_test_pred)
        print("Test Accuracy: {:.4f}".format(test_acc))
        test_report = classification_report(y_test_encoded, y_test_pred)
        print("Test Classification Report:\n", test_report)

        # Save results for the current aspect
        best_models[aspect.lower()] = {
            "model": best_cv_estimator,
            "label_encoder": le
        }
        train_reports[aspect.lower()] = train_report
        test_reports[aspect.lower()] = test_report

    return best_models, train_reports, test_reports


In [ ]:
best_models, train_reports, test_reports = train_final_models_grid_search(train_df,test_df, aspects)


=== Processing aspect: Acting ===


/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Best parameters for aspect 'Acting': {'clf__max_depth': None, 'clf__min_samples_leaf': 4, 'clf__min_samples_split': 2, 'clf__n_estimators': 100}
0.5876176636470755
0.849509767548402
Average 10-fold CV test Accuracy for aspect 'Acting': 0.5876
Average 10-fold CV train Accuracy for aspect 'Acting': 0.8495
Final Training Accuracy: 0.8432
Final Training Classification Report:
               precision    recall  f1-score   support

           0       0.39      0.82      0.53       131
           1       0.94      0.86      0.90      2962
           2       0.70      0.79      0.74       848

    accuracy                           0.84      3941
   macro avg       0.68      0.82      0.72      3941
weighted avg       0.87      0.84      0.85      3941

Test Accuracy: 0.7647
Test Classification Report:
               precision    recall  f1-score   support

           0       0.08      0.15      0.10        34
           1       0.88      0.83      0.86       746
           2       0.58      

/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Best parameters for aspect 'direction': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 5, 'clf__n_estimators': 200}
0.6281640005642024
0.8807144052008189
Average 10-fold CV test Accuracy for aspect 'direction': 0.6282
Average 10-fold CV train Accuracy for aspect 'direction': 0.8807
Final Training Accuracy: 0.8533
Final Training Classification Report:
               precision    recall  f1-score   support

           0       0.56      0.86      0.68       568
           1       0.98      0.85      0.91      3128
           2       0.61      0.89      0.73       245

    accuracy                           0.85      3941
   macro avg       0.72      0.86      0.77      3941
weighted avg       0.89      0.85      0.86      3941

Test Accuracy: 0.7353
Test Classification Report:
               precision    recall  f1-score   support

           0       0.31      0.54      0.40       124
           1       0.90      0.78      0.84       804
           2       

/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Best parameters for aspect 'Music': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 10, 'clf__n_estimators': 100}
0.6997706455746728
0.9447002163943724
Average 10-fold CV test Accuracy for aspect 'Music': 0.6998
Average 10-fold CV train Accuracy for aspect 'Music': 0.9447
Final Training Accuracy: 0.9635
Final Training Classification Report:
               precision    recall  f1-score   support

           0       0.68      0.92      0.78        89
           1       0.99      0.97      0.98      3446
           2       0.81      0.89      0.85       406

    accuracy                           0.96      3941
   macro avg       0.83      0.93      0.87      3941
weighted avg       0.97      0.96      0.96      3941

Test Accuracy: 0.9422
Test Classification Report:
               precision    recall  f1-score   support

           0       0.39      0.39      0.39        18
           1       0.98      0.97      0.98       867
           2       0.73      0

/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Best parameters for aspect 'ovr_sent': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 5, 'clf__n_estimators': 50}
0.6318667805871323
0.8118891416698295
Average 10-fold CV test Accuracy for aspect 'ovr_sent': 0.6319
Average 10-fold CV train Accuracy for aspect 'ovr_sent': 0.8119
Final Training Accuracy: 0.7968
Final Training Classification Report:
               precision    recall  f1-score   support

           0       0.78      0.82      0.80      1346
           1       0.56      0.78      0.65       567
           2       0.91      0.79      0.85      2028

    accuracy                           0.80      3941
   macro avg       0.75      0.80      0.77      3941
weighted avg       0.82      0.80      0.80      3941

Test Accuracy: 0.6663
Test Classification Report:
               precision    recall  f1-score   support

           0       0.67      0.67      0.67       348
           1       0.35      0.55      0.43       139
           2       0.82

In [ ]:
sample_sentence = "vijay anna mass vera level "
predictions = predict_all_aspects(sample_sentence, best_models)

print("\nPredictions for the sample sentence:")
for aspect, pred in predictions.items():
    print(f"{aspect.capitalize()}: {pred}")


Predictions for the sample sentence:
Acting: 1
Direction: 0
Music: 0
Genre: 0
Excitement: 1
Ovr_sent: 1


In [ ]:
best_models

{'acting': {'model': Pipeline(steps=[('tfidf',
                   TfidfVectorizer(max_df=0.95, max_features=5000, min_df=2,
                                   ngram_range=(1, 2))),
                  ('clf',
                   RandomForestClassifier(min_samples_leaf=2, min_samples_split=5,
                                          random_state=42))]),
  'label_encoder': LabelEncoder()},
 'direction': {'model': Pipeline(steps=[('tfidf',
                   TfidfVectorizer(max_df=0.95, max_features=5000, min_df=2,
                                   ngram_range=(1, 2))),
                  ('clf',
                   RandomForestClassifier(min_samples_split=10, n_estimators=200,
                                          random_state=42))]),
  'label_encoder': LabelEncoder()},
 'music': {'model': Pipeline(steps=[('tfidf',
                   TfidfVectorizer(max_df=0.95, max_features=5000, min_df=2,
                                   ngram_range=(1, 2))),
                  ('clf',
              

In [ ]:
df = pd.read_csv("Romanised_fyp_data.csv")

def train_final_models_grid_search(df, aspects):
    """
    For each aspect, perform a grid search to find the best SVC parameters using a pipeline.
    Uses an 80/20 train-test split, prints training and test accuracy and classification reports,
    and returns the best models along with their label encoders.
    """
    best_models = {}
    train_reports = {}
    test_reports = {}

    # Define a parameter grid for the SVC inside a pipeline
    param_grid = {
        'clf__n_estimators': [50, 100, 200],
        'clf__max_depth': [None, 10, 20, 30],
        'clf__min_samples_split': [2, 5, 10],
        'clf__min_samples_leaf': [1, 2, 4]
    }

    for aspect in aspects:
        print(f"\n=== Processing aspect: {aspect} ===")
        X, y = prepare_data(df, aspect)
        # Encode target labels to numerical values
        le = LabelEncoder()
        y_encoded = le.fit_transform(y)

        # Split data into training and testing sets (80/20 split)
        X_train, X_test, y_train, y_test = train_test_split(
            X, y_encoded, test_size=0.2, random_state=42, stratify=y_encoded
        )

        # Create a pipeline: first vectorize text, then classify with SVC
        pipeline = Pipeline([
            ('tfidf', TfidfVectorizer(max_features=5000,
                                      ngram_range=(1, 2),
                                      min_df=2,
                                      max_df=0.95)),
            ('clf', RandomForestClassifier(random_state=42))
        ])

        # Set up GridSearchCV with 5-fold cross-validation
        cv_strategy = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
        grid = GridSearchCV(pipeline, param_grid, cv=cv_strategy, scoring='accuracy', n_jobs=-1)
        grid.fit(X_train['R_clean_text'], y_train)

        print(f"Best parameters for aspect '{aspect}': {grid.best_params_}")

        best_estimator = grid.best_estimator_

        # Evaluate on training data
        y_train_pred = best_estimator.predict(X_train['R_clean_text'])
        train_acc = accuracy_score(y_train, y_train_pred)
        print("Training Accuracy: {:.4f}".format(train_acc))
        train_report = classification_report(y_train, y_train_pred)
        print("Training Classification Report:\n", train_report)

        # Evaluate on test data
        y_test_pred = best_estimator.predict(X_test['R_clean_text'])
        test_acc = accuracy_score(y_test, y_test_pred)
        print("Test Accuracy: {:.4f}".format(test_acc))
        test_report = classification_report(y_test, y_test_pred)
        print("Test Classification Report:\n", test_report)

        best_models[aspect.lower()] = {
            "model": best_estimator,
            "label_encoder": le
        }
        train_reports[aspect.lower()] = train_report
        test_reports[aspect.lower()] = test_report

    return best_models, train_reports, test_reports

def prepare_data(df, aspect_column):
  """Prepare data for a specific aspect"""
  # Encode text to numerical values if needed
  # le = LabelEncoder()
  # Changed to return a DataFrame instead of a Series
  X = df[['R_clean_text']]
  y = df[aspect_column]
  return X, y

In [ ]:
aspects = ['Acting', 'direction', 'Music', 'ovr_sent']

In [ ]:
best_models, train_reports, test_reports = train_final_models_grid_search(df, aspects)


=== Processing aspect: Acting ===
Best parameters for aspect 'Acting': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 2, 'clf__n_estimators': 50}
Training Accuracy: 0.9008
Training Classification Report:
               precision    recall  f1-score   support

           0       1.00      0.08      0.14       132
           1       0.91      0.98      0.94      2966
           2       0.86      0.76      0.81       843

    accuracy                           0.90      3941
   macro avg       0.92      0.61      0.63      3941
weighted avg       0.90      0.90      0.89      3941

Test Accuracy: 0.8418
Test Classification Report:
               precision    recall  f1-score   support

           0       0.00      0.00      0.00        33
           1       0.88      0.94      0.91       742
           2       0.69      0.64      0.67       211

    accuracy                           0.84       986
   macro avg       0.52      0.53      0.52       986
weig

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


Best parameters for aspect 'direction': {'clf__max_depth': None, 'clf__min_samples_leaf': 1, 'clf__min_samples_split': 10, 'clf__n_estimators': 200}
Training Accuracy: 0.9827
Training Classification Report:
               precision    recall  f1-score   support

           0       0.99      0.93      0.96       554
           1       0.98      1.00      0.99      3145
           2       0.96      0.90      0.93       242

    accuracy                           0.98      3941
   macro avg       0.98      0.94      0.96      3941
weighted avg       0.98      0.98      0.98      3941

Test Accuracy: 0.8276
Test Classification Report:
               precision    recall  f1-score   support

           0       0.57      0.17      0.26       138
           1       0.85      0.97      0.91       787
           2       0.61      0.44      0.51        61

    accuracy                           0.83       986
   macro avg       0.68      0.53      0.56       986
weighted avg       0.80      0.83 

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


Best parameters for aspect 'excitement': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 5, 'clf__n_estimators': 200}
Training Accuracy: 0.8155
Training Classification Report:
               precision    recall  f1-score   support

           0       0.92      0.51      0.65       594
           1       0.79      0.94      0.86      2244
           2       0.85      0.73      0.79      1103

    accuracy                           0.82      3941
   macro avg       0.85      0.73      0.77      3941
weighted avg       0.83      0.82      0.81      3941

Test Accuracy: 0.6734
Test Classification Report:
               precision    recall  f1-score   support

           0       0.59      0.20      0.30       148
           1       0.67      0.86      0.75       562
           2       0.70      0.55      0.62       276

    accuracy                           0.67       986
   macro avg       0.65      0.54      0.56       986
weighted avg       0.67      0.67 

In [ ]:
train_df = pd.read_csv("Romanised_train_data.csv")
test_df = pd.read_csv("Romanised_test_data.csv")
def train_final_models_grid_search(train_df, test_df, aspects):
    """
    For each aspect:
    1. Perform grid search on the training data to find the best parameters.
    2. Using the best parameters, perform 10-fold cross-validation,
       returning both the average accuracy and the list of fold estimators.
    3. Select the best estimator from CV (highest test score) and evaluate it on test data.
    Returns the best models along with their label encoders and classification reports.
    """
    best_models = {}
    train_reports = {}
    test_reports = {}

    # Parameter grid for the classifier
    param_grid = {
        'clf__n_estimators': [50, 100, 200],
        'clf__max_depth': [None],
        'clf__min_samples_split': [2, 5, 10],
        'clf__min_samples_leaf': [2, 4, 8]
    }

    for aspect in aspects:
        print(f"\n=== Processing aspect: {aspect} ===")
        # Prepare data for current aspect
        X_train, y_train = prepare_data(train_df, aspect)
        X_test, y_test = prepare_data(test_df, aspect)

        # Encode target labels to numerical values
        le = LabelEncoder()
        y_train_encoded = le.fit_transform(y_train)
        y_test_encoded = le.fit_transform(y_test)

        # Build initial pipeline with a placeholder classifier
        pipeline = Pipeline([
            ('tfidf', TfidfVectorizer(max_features=5000,
                                      ngram_range=(1, 2),
                                      min_df=5,
                                      max_df=0.90,
                                      tokenizer=custom_tokenizer)),
            ('clf', RandomForestClassifier(random_state=42, class_weight='balanced'))
        ])

        # 10-fold CV strategy for grid search
        cv_strategy = StratifiedKFold(n_splits=10, shuffle=True, random_state=42)

        # Ensure there are no missing or empty texts in training set
        X_train = X_train.dropna(subset=['R_clean_text'])
        X_train = X_train[X_train['R_clean_text'].str.strip() != '']

        # --- Step 1: Grid Search ---
        grid = GridSearchCV(pipeline, param_grid, cv=cv_strategy,
                            scoring='balanced_accuracy', n_jobs=-1, return_train_score=True)
        grid.fit(X_train['R_clean_text'], y_train_encoded)
        best_params = grid.best_params_
        print(f"Best parameters for aspect '{aspect}': {best_params}")

        # --- Step 2: Build a new pipeline using the best parameters ---
        best_pipeline = Pipeline([
            ('tfidf', TfidfVectorizer(max_features=5000,
                                      ngram_range=(1, 2),
                                      min_df=5,
                                      max_df=0.90,
                                      tokenizer=custom_tokenizer)),
            ('clf', RandomForestClassifier(random_state=42,
                                             class_weight='balanced',
                                             n_estimators=best_params['clf__n_estimators'],
                                             max_depth=best_params['clf__max_depth'],
                                             min_samples_split=best_params['clf__min_samples_split'],
                                             min_samples_leaf=best_params['clf__min_samples_leaf']))
        ])

        # --- Step 3: Perform 10-Fold Cross Validation with estimator return ---
        cv_results = cross_validate(best_pipeline, X_train['R_clean_text'], y_train_encoded,
                                    cv=StratifiedKFold(n_splits=10, shuffle=True, random_state=42),
                                    scoring='balanced_accuracy', return_train_score=True,return_estimator=True, n_jobs=-1)
        avg_cv_score_test = cv_results['test_score'].mean()
        avg_cv_score_train = cv_results['train_score'].mean()
        print(avg_cv_score_test)
        print(avg_cv_score_train)


        print(f"Average 10-fold CV test Accuracy for aspect '{aspect}': {avg_cv_score_test:.4f}")
        print(f"Average 10-fold CV train Accuracy for aspect '{aspect}': {avg_cv_score_train:.4f}")

        # --- Step 4: Select the best estimator from the CV folds ---
        best_index = np.argmax(cv_results['test_score'])
        best_cv_estimator = cv_results['estimator'][best_index]

        # Evaluate the selected estimator on the training data (optional)
        y_train_pred = best_cv_estimator.predict(X_train['R_clean_text'])
        train_acc = accuracy_score(y_train_encoded, y_train_pred)
        print("Final Training Accuracy: {:.4f}".format(train_acc))
        train_report = classification_report(y_train_encoded, y_train_pred)
        print("Final Training Classification Report:\n", train_report)

        # --- Step 5: Evaluate on Test Data ---
        y_test_pred = best_cv_estimator.predict(X_test['R_clean_text'])
        test_acc = accuracy_score(y_test_encoded, y_test_pred)
        print("Test Accuracy: {:.4f}".format(test_acc))
        test_report = classification_report(y_test_encoded, y_test_pred)
        print("Test Classification Report:\n", test_report)

        # Save results for the current aspect
        best_models[aspect.lower()] = {
            "model": best_cv_estimator,
            "label_encoder": le
        }
        train_reports[aspect.lower()] = train_report
        test_reports[aspect.lower()] = test_report

    return best_models, train_reports, test_reports

def prepare_data(df, aspect_column):
  """Prepare data for a specific aspect"""
  # Encode text to numerical values if needed
  # le = LabelEncoder()
  # Changed to return a DataFrame instead of a Series
  X = df[['R_clean_text']]
  y = df[aspect_column]
  return X, y

In [ ]:
best_models, train_reports, test_reports = train_final_models_grid_search(train_df,test_df, aspects)


=== Processing aspect: Acting ===


/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Best parameters for aspect 'Acting': {'clf__max_depth': None, 'clf__min_samples_leaf': 4, 'clf__min_samples_split': 10, 'clf__n_estimators': 200}
0.5842225588304019
0.8554512992640857
Average 10-fold CV test Accuracy for aspect 'Acting': 0.5842
Average 10-fold CV train Accuracy for aspect 'Acting': 0.8555
Final Training Accuracy: 0.8597
Final Training Classification Report:
               precision    recall  f1-score   support

           0       0.45      0.84      0.59       131
           1       0.94      0.88      0.91      2962
           2       0.72      0.79      0.76       848

    accuracy                           0.86      3941
   macro avg       0.71      0.84      0.75      3941
weighted avg       0.88      0.86      0.87      3941

Test Accuracy: 0.7779
Test Classification Report:
               precision    recall  f1-score   support

           0       0.13      0.24      0.17        34
           1       0.89      0.84      0.86       746
           2       0.60    

/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Best parameters for aspect 'direction': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 5, 'clf__n_estimators': 50}
0.629459538191756
0.8673589700959603
Average 10-fold CV test Accuracy for aspect 'direction': 0.6295
Average 10-fold CV train Accuracy for aspect 'direction': 0.8674
Final Training Accuracy: 0.8439
Final Training Classification Report:
               precision    recall  f1-score   support

           0       0.55      0.84      0.66       568
           1       0.98      0.84      0.90      3128
           2       0.58      0.88      0.70       245

    accuracy                           0.84      3941
   macro avg       0.70      0.85      0.76      3941
weighted avg       0.89      0.84      0.86      3941

Test Accuracy: 0.7505
Test Classification Report:
               precision    recall  f1-score   support

           0       0.33      0.55      0.41       124
           1       0.91      0.79      0.85       804
           2       0.

/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Best parameters for aspect 'Music': {'clf__max_depth': None, 'clf__min_samples_leaf': 4, 'clf__min_samples_split': 10, 'clf__n_estimators': 100}
0.7059227701646751
0.9093470067400743
Average 10-fold CV test Accuracy for aspect 'Music': 0.7059
Average 10-fold CV train Accuracy for aspect 'Music': 0.9093
Final Training Accuracy: 0.9523
Final Training Classification Report:
               precision    recall  f1-score   support

           0       0.58      0.91      0.71        89
           1       0.99      0.97      0.98      3446
           2       0.80      0.82      0.81       406

    accuracy                           0.95      3941
   macro avg       0.79      0.90      0.83      3941
weighted avg       0.96      0.95      0.95      3941

Test Accuracy: 0.9270
Test Classification Report:
               precision    recall  f1-score   support

           0       0.24      0.39      0.30        18
           1       0.98      0.96      0.97       867
           2       0.70      0

/usr/local/lib/python3.11/dist-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Best parameters for aspect 'ovr_sent': {'clf__max_depth': None, 'clf__min_samples_leaf': 2, 'clf__min_samples_split': 10, 'clf__n_estimators': 200}
0.635072994957137
0.8122908986798952
Average 10-fold CV test Accuracy for aspect 'ovr_sent': 0.6351
Average 10-fold CV train Accuracy for aspect 'ovr_sent': 0.8123
Final Training Accuracy: 0.7995
Final Training Classification Report:
               precision    recall  f1-score   support

           0       0.77      0.84      0.80      1346
           1       0.58      0.76      0.66       567
           2       0.92      0.78      0.85      2028

    accuracy                           0.80      3941
   macro avg       0.76      0.80      0.77      3941
weighted avg       0.82      0.80      0.80      3941

Test Accuracy: 0.6694
Test Classification Report:
               precision    recall  f1-score   support

           0       0.67      0.67      0.67       348
           1       0.35      0.54      0.42       139
           2       0.8

Save the models

In [ ]:
import pickle
import os

def save_models(models, filename="final_models.pkl"):
    """Save trained models and label encoders to a pickle file."""
    with open(filename, 'wb') as f:
        pickle.dump(models, f)
    print(f"Models saved to {filename}")

def load_models(filename="final_models.pkl"):
    """Load trained models and label encoders from a pickle file."""
    if not os.path.exists(filename):
        raise FileNotFoundError(f"The file {filename} does not exist.")
    with open(filename, 'rb') as f:
        models = pickle.load(f)
    print(f"Models loaded from {filename}")
    return models

def predict_all_aspects_from_file(sentence, model_filename="final_models.pkl"):
    """Load the saved models and predict aspects for a given sentence."""
    models = load_models(model_filename)
    predictions = {}

    for aspect, model_info in models.items():
        model = model_info['model']
        le = model_info['label_encoder']
        pred_encoded = model.predict([sentence])[0]
        pred_label = le.inverse_transform([pred_encoded])[0]
        predictions[aspect] = pred_label

    return predictions

In [ ]:
# save_models(best_models)  # Call this after training to save models
# predictions = predict_all_aspects_from_file("The movie had great visuals but weak acting.")

In [ ]:
import shap
shap.initjs()

import numpy as np

def explain_prediction_rf(aspect, sentence, final_models, background_texts=None, class_idx=0):
    """
    Generates a SHAP force plot to explain the prediction for a given sentence
    for the specified aspect using a RandomForestClassifier-based pipeline.

    Parameters:
    - aspect: The aspect (string) for which to explain the prediction.
    - sentence: The raw text input to explain.
    - final_models: Dictionary returned by train_final_models_grid_search.
    - background_texts: Optional list of sentences for the background sample.
      If None, a default small sample is used.
    - class_idx: The class index to explain (default 0).

    Returns:
    - A SHAP force plot visualization.
    """
    # Retrieve the trained pipeline and label encoder for the given aspect.
    model_info = final_models[aspect.lower()]
    pipeline = model_info['model']

    # Extract the vectorizer and RandomForestClassifier from the pipeline.
    vectorizer = pipeline.named_steps['tfidf']
    clf = pipeline.named_steps['clf']

    # Define a small background sample for SHAP, if none is provided.
    if background_texts is None:
        background_texts = [
            "This is a sample sentence.",
            "Another example of text input.",
            "Additional background sentence."
        ]

    # Transform the background texts to the vectorized feature space.
    X_background = vectorizer.transform(background_texts)
    X_background_dense = X_background.toarray()  # Convert to dense format for TreeExplainer

    # Initialize TreeExplainer for the RandomForestClassifier.
    explainer = shap.TreeExplainer(clf, X_background_dense)

    # Transform the input sentence using the same vectorizer.
    X_instance = vectorizer.transform([sentence])
    X_instance_dense = X_instance.toarray()  # Shape (1, n_features)

    # Compute SHAP values.
    shap_values = explainer.shap_values(X_instance_dense)

    # Handle multi-output (multi-class) SHAP values:
    if isinstance(shap_values, np.ndarray) and shap_values.ndim == 3:
        # shap_values shape: (1, n_features, n_classes)
        shap_value = shap_values[0, :, class_idx]  # Extract 1D vector for sample 0 and class 'class_idx'
        expected_value = explainer.expected_value[class_idx] if isinstance(explainer.expected_value, (list, np.ndarray)) else explainer.expected_value
    elif isinstance(shap_values, list):
        # In some cases shap_values is returned as a list of arrays.
        shap_value = shap_values[class_idx][0]  # Extract the 1D explanation vector for the chosen class
        expected_value = explainer.expected_value[class_idx] if isinstance(explainer.expected_value, (list, np.ndarray)) and len(explainer.expected_value) > 1 else explainer.expected_value
    else:
        shap_value = shap_values[0]
        expected_value = explainer.expected_value

    # Get feature names from the vectorizer.
    feature_names = vectorizer.get_feature_names_out()

    # Initialize JS visualization (for notebooks or compatible environments).
    shap.initjs()

    # Use the new force plot API: pass the base (expected) value, the 1D shap values,
    # and the corresponding feature values.
    force_plot = shap.plots.force(
        expected_value,
        shap_value,
        features=X_instance_dense[0],
        feature_names=feature_names
    )

    return force_plot

# Example usage:
# explanation = explain_prediction_rf("Acting", "This movie had outstanding performances!", best_models)


In [ ]:
# Example usage:
# Assuming final_models is the output from train_final_models_grid_search and you want to explain a prediction for "Acting"
shap.initjs()
explanation_Act = explain_prediction_rf("acting", "vijay anna mass vera level", best_models)
explanation_Act_1 = explain_prediction_rf("acting", "vijay anna mass vera level", best_models,class_idx=1)
explanation_Act_2 = explain_prediction_rf("acting", "vijay anna mass vera level", best_models,class_idx=2)

# explanation_dir = explain_prediction_rf("direction", "vijay anna mass vera level", best_models)
# explanation_ovr = explain_prediction_rf("ovr_sent", "vijay anna mass vera level", best_models)

# The 'explanation' variable now holds the SHAP force plot which you can display in a Jupyter notebook or compatible environment.

In [ ]:
shap.initjs()
explanation_Act


In [ ]:
shap.initjs()
explanation_Act_1


In [ ]:
shap.initjs()
explanation_Act_2

In [ ]:
explanation_ovr = explain_prediction_rf("ovr_sent", "vera leval pa summa therikka vittutaanga", best_models)
explanation_ovr_1 = explain_prediction_rf("ovr_sent", "vera leval pa summa therikka vittutaanga", best_models,class_idx = 1)
explanation_ovr_2 = explain_prediction_rf("ovr_sent", "vera leval pa summa therikka vittutaanga", best_models,class_idx = 2)

In [ ]:
shap.initjs()
explanation_ovr

In [ ]:
shap.initjs()
explanation_ovr_1

In [ ]:
shap.initjs()
explanation_ovr_2